In [1]:
import matplotlib.pyplot as plt
from datetime import datetime, timedelta
import plotly.graph_objects as go
import datetime
import pandas as pd
import csv
import os
import time
from dateutil import tz
import glob
import quandl as q
import re
import plotly.graph_objects as go
import numpy as np
import streamlit as st
from plotly.subplots import make_subplots

st.set_page_config(layout="wide")
# %%
from fredapi import Fred

In [2]:
api_key_fred = os.environ['api_key_fred']
fred = Fred(api_key=api_key_fred)

quandl_api_key = os.environ['quandl_api_key']


In [3]:
# # # start - read in BTC data # # #
datasource_btcusd = "BITFINEX/DOGEUSD.csv"
# dogeusd_data = pd.read_csv("coindata/{}".format(
#     datasource_btcusd.replace("/", " ")), index_col=0)
# dogeusd_data.index = pd.to_datetime(dogeusd_data.index)

# most_recent_stored_btcusd_date = dogeusd_data.sort_index().tail(1).index[0].strftime("%Y-%m-%d")
todays_date = datetime.date.today() - timedelta(days=1)
todays_date = todays_date.strftime("%Y-%m-%d")

data = q.get(datasource_btcusd.split(".")[0],   start_date='2017-01-01',
                 end_date='{}'.format(todays_date),
                 api_key=quandl_api_key)
data.info()
data["First"] = data.Last.shift(1)
data = data.dropna()
data

<class 'pandas.core.frame.DataFrame'>
DatetimeIndex: 835 entries, 2021-04-21 to 2023-08-03
Data columns (total 7 columns):
 #   Column  Non-Null Count  Dtype  
---  ------  --------------  -----  
 0   High    835 non-null    float64
 1   Low     835 non-null    float64
 2   Mid     835 non-null    float64
 3   Last    835 non-null    float64
 4   Bid     835 non-null    float64
 5   Ask     835 non-null    float64
 6   Volume  835 non-null    float64
dtypes: float64(7)
memory usage: 52.2 KB


High       Low       Mid      Last       Bid       Ask  \
Date                                                                     
2021-04-22  0.310190  0.254200  0.263865  0.266120  0.263390  0.264340   
2021-04-23  0.268080  0.179490  0.243185  0.243570  0.242950  0.243420   
2021-04-24  0.290000  0.228900  0.270640  0.271600  0.270350  0.270930   
2021-04-25  0.289400  0.225320  0.250750  0.250880  0.250350  0.251150   
2021-04-26  0.280660  0.248000  0.269230  0.269110  0.268930  0.269530   
...              ...       ...       ...       ...       ...       ...   
2023-07-30  0.080720  0.076360  0.077813  0.077814  0.077813  0.077814   
2023-07-31  0.079879  0.076834  0.077784  0.077798  0.077769  0.077798   
2023-08-01  0.078382  0.075459  0.077238  0.077276  0.077199  0.077276   
2023-08-02  0.078364  0.073856  0.074621  0.074654  0.074604  0.074638   
2023-08-03  0.075092  0.072662  0.073835  0.073821  0.073813  0.073857   

                  Volume     First  
Date                                
2021-04-22  3.914806e+07  0.308760  
2021-04-23  7.169683e+07  0.266120  
2021-04-24  3.672039e+07  0.243570  
2021-04-25  1.529839e+07  0.271600  
2021-04-26  1.969569e+07  0.250880  
...                  ...       ...  
2023-07-30  6.559048e+06  0.080522  
2023-07-31  4.114400e+06  0.077814  
2023-08-01  4.528323e+06  0.077798  
2023-08-02  3.529204e+06  0.077276  
2023-08-03  3.420566e+06  0.074654  

[834 rows x 8 columns]

In [4]:
dogeusd_data = data.sort_index()
# store current df with up-to-date values
dogeusd_data.to_csv('coindata/{}'.format(
    datasource_btcusd.replace("/", " ")), index=True)

In [5]:
# # # start - data processing # # #
dogeusd_data = dogeusd_data.dropna()
dogeusd_data["350_movingaverage"] = pd.Series.rolling(
    dogeusd_data["Last"], window=350, min_periods=1).mean()
dogeusd_data["111_movingaverage"] = pd.Series.rolling(
    dogeusd_data["Last"], window=111, min_periods=1).mean()
# # # end - data processing # # #


In [6]:
# run_it = st.sidebar.button('Show visualizations')

# TODO: Future integrate ETH
# display_name_all_twitter_user_scraped_csvs, all_twitter_user_scraped_csvs = get_all_stored_crypto_csvs()
# display_name_user_selection_list_containing_twitter_user = st.sidebar.selectbox(
#     "Select existing Twitter-User", list(display_name_all_twitter_user_scraped_csvs), 0)


In [7]:
# # # start - get data from fred api and store csv # # #
# # GET S&P DATA
# Billions of Dollars 
data_SP500 = fred.get_series('SP500')
data_SP500 = data_SP500.sort_index()
# store current df with up-to-date values
data_SP500.to_csv('coindata/data_SP500.csv', index=True)

# # Assets: Total Assets: Total Assets: Wednesday Level (RESPPANWW)
#Assets: Total Assets: Total Assets: Wednesday Level (RESPPANWW) Millions of Dollars
data_WALCL = fred.get_series('WALCL')
data_WALCL.dropna()
data_WALCL = data_WALCL.sort_index()
# store current df with up-to-date values
data_WALCL.to_csv('coindata/data_WALCL.csv', index=True)

# # Overnight Reverse Repurchase Agreements Treasury Securities Sold by the Federal Reserve in the Temporary Open Market Operations (RRPONTSYD)
data_RRPONTSYD = fred.get_series('RRPONTSYD')
#Assets: Total Assets: Total Assets: Wednesday Level (RESPPANWW)
# Billions of U.S. Dollars
# data_FRED_RRPONTSYD.values = data_FRED_RRPONTSYD.values * 1000 
data_RRPONTSYD = data_RRPONTSYD * 1000 
data_RRPONTSYD.dropna()
data_RRPONTSYD = data_RRPONTSYD.sort_index()
# store current df with up-to-date values
data_RRPONTSYD.to_csv('coindata/data_RRPONTSYD.csv', index=True)

# # Deposits with Federal Reserve Banks, other than Reserve Balances: U.S. Treasury, General Account (WTREGEN)
# Billions of Dollars 
data_FRED_WTREGEN = fred.get_series('WTREGEN')
data_FRED_WTREGEN = data_FRED_WTREGEN * 1000

data_FRED_WTREGEN.dropna()
data_FRED_WTREGEN = data_FRED_WTREGEN.sort_index()
# store current df with up-to-date values
data_FRED_WTREGEN.to_csv('coindata/data_FRED_WTREGEN.csv', index=True)

# # net liquidity vs s&p500 weekly - Diagram
datasource_fred_total_assets = "data_WALCL.csv"
fred_total_assets = pd.read_csv("coindata/{}".format(
    datasource_fred_total_assets.replace("/", " ")), index_col=0)
fred_total_assets.index = pd.to_datetime(fred_total_assets.index)

most_recent_stored_fred_rrpontsyd_date = fred_total_assets.sort_index().tail(
    1).index[0].strftime("%Y-%m-%d")
todays_date = datetime.date.today() - timedelta(days=1)
todays_date = todays_date.strftime("%Y-%m-%d")

datasource_FRED_WTREGEN = "data_FRED_WTREGEN.csv"
FRED_WTREGEN_data = pd.read_csv("coindata/{}".format(
    datasource_FRED_WTREGEN.replace("/", " ")), index_col=0)
FRED_WTREGEN_data.index = pd.to_datetime(FRED_WTREGEN_data.index)

most_recent_stored_FRED_WTREGEN_date = FRED_WTREGEN_data.sort_index().tail(
    1).index[0].strftime("%Y-%m-%d")

datasource_FRED_RRPONTSYD = "data_RRPONTSYD.csv"
FRED_RRPONTSYD_data = pd.read_csv("coindata/{}".format(
    datasource_FRED_RRPONTSYD.replace("/", " ")), index_col=0)
FRED_RRPONTSYD_data.index = pd.to_datetime(FRED_RRPONTSYD_data.index)

most_recent_stored_FRED_RRPONTSYD_date = FRED_RRPONTSYD_data.sort_index().tail(
    1).index[0].strftime("%Y-%m-%d")

# # # end - get data from fred api and store csv # # #

In [8]:
dogeusd_data = dogeusd_data[(dogeusd_data.index > '2020-08-11 00:00:00')]

In [9]:
import warnings
warnings.filterwarnings("ignore")
from astral import moon
import datetime

# take the data_SP500 index and iterate over it to get the moon phase for each day
# the make a new df out of it called df_moon_phase
df_moon_phase = pd.DataFrame()
for i in data_SP500.index:
    df_moon_phase = df_moon_phase.append({"date": i, "moon_phase": moon.phase(i)}, ignore_index=True)

df_moon_phase["moon_phase"] = df_moon_phase["moon_phase"].astype(int)
df_moon_phase["date"] = pd.to_datetime(df_moon_phase["date"])
df_moon_phase["date"] = df_moon_phase["date"].dt.date
df_moon_phase = df_moon_phase.set_index("date")

# check the relationship between moon phase and dogeusd_data
# merge sp500 with moon phase
dogeusd_data_and_moon_phase = pd.merge(
    dogeusd_data, df_moon_phase, left_index=True, right_index=True, how='left')
dogeusd_data_and_moon_phase = dogeusd_data_and_moon_phase.dropna()
dogeusd_data_and_moon_phase["350_movingaverage"] = pd.Series.rolling(
    dogeusd_data_and_moon_phase["Last"], window=350, min_periods=1).mean()
dogeusd_data_and_moon_phase["111_movingaverage"] = pd.Series.rolling(
    dogeusd_data_and_moon_phase["Last"], window=111, min_periods=1).mean()

# calculat the daily price change for dogeusd_data_and_moon_phase in percentage
dogeusd_data_and_moon_phase["daily_price_change"] = dogeusd_data_and_moon_phase["Last"].pct_change()
dogeusd_data_and_moon_phase["daily_price_change"] = dogeusd_data_and_moon_phase["daily_price_change"].fillna(0)
# calculat the daily price change for dogeusd_data_and_moon_phase in absolut values
dogeusd_data_and_moon_phase["daily_price_change_abs"] = dogeusd_data_and_moon_phase["Last"].diff()
dogeusd_data_and_moon_phase["daily_price_change_abs"] = dogeusd_data_and_moon_phase["daily_price_change_abs"].fillna(0)
dogeusd_data_and_moon_phase

High       Low       Mid      Last       Bid       Ask  \
Date                                                                     
2021-04-22  0.310190  0.254200  0.263865  0.266120  0.263390  0.264340   
2021-04-23  0.268080  0.179490  0.243185  0.243570  0.242950  0.243420   
2021-04-26  0.280660  0.248000  0.269230  0.269110  0.268930  0.269530   
2021-04-27  0.280080  0.265080  0.271455  0.271210  0.271230  0.271680   
2021-04-28  0.344710  0.255940  0.318290  0.318830  0.318070  0.318510   
...              ...       ...       ...       ...       ...       ...   
2023-07-28  0.077977  0.076128  0.077591  0.077560  0.077570  0.077612   
2023-07-31  0.079879  0.076834  0.077784  0.077798  0.077769  0.077798   
2023-08-01  0.078382  0.075459  0.077238  0.077276  0.077199  0.077276   
2023-08-02  0.078364  0.073856  0.074621  0.074654  0.074604  0.074638   
2023-08-03  0.075092  0.072662  0.073835  0.073821  0.073813  0.073857   

                  Volume     First  350_movingaverage  111_movingaverage  \
Date                                                                       
2021-04-22  3.914806e+07  0.308760           0.266120           0.266120   
2021-04-23  7.169683e+07  0.266120           0.254845           0.254845   
2021-04-26  1.969569e+07  0.250880           0.259600           0.259600   
2021-04-27  1.280031e+07  0.269110           0.262503           0.262503   
2021-04-28  4.295062e+07  0.271210           0.273768           0.273768   
...                  ...       ...                ...                ...   
2023-07-28  4.153710e+06  0.077365           0.081208           0.074039   
2023-07-31  4.114400e+06  0.077814           0.081011           0.074009   
2023-08-01  4.528323e+06  0.077798           0.080822           0.073972   
2023-08-02  3.529204e+06  0.077276           0.080625           0.073918   
2023-08-03  3.420566e+06  0.074654           0.080439           0.073845   

            moon_phase  daily_price_change  daily_price_change_abs  
Date                                                                
2021-04-22         9.0            0.000000                0.000000  
2021-04-23        10.0           -0.084736               -0.022550  
2021-04-26        13.0            0.104857                0.025540  
2021-04-27        14.0            0.007804                0.002100  
2021-04-28        15.0            0.175583                0.047620  
...                ...                 ...                     ...  
2023-07-28         9.0            0.002521                0.000195  
2023-07-31        12.0            0.003069                0.000238  
2023-08-01        13.0           -0.006710               -0.000522  
2023-08-02        14.0           -0.033930               -0.002622  
2023-08-03        15.0           -0.011158               -0.000833  

[596 rows x 13 columns]

In [10]:
# now we want the relationship of the moon_phase column on the daily_price_change and daily_price_change_abs column
# we group by the moon_phase column and calculate the mean of the daily_price_change and daily_price_change_abs column
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase.groupby("moon_phase").mean()
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase_grouped.reset_index()
dogeusd_data_and_moon_phase_grouped


moon_phase      High       Low       Mid      Last       Bid       Ask  \
0          0.0  0.167800  0.150045  0.157203  0.157192  0.157128  0.157278   
1          1.0  0.140844  0.124019  0.135327  0.135267  0.135226  0.135428   
2          2.0  0.149344  0.134378  0.143363  0.143352  0.143295  0.143430   
3          3.0  0.145262  0.133185  0.138508  0.138537  0.138446  0.138569   
4          4.0  0.153300  0.141289  0.146592  0.146630  0.146525  0.146658   
5          5.0  0.150686  0.138979  0.143089  0.143092  0.143030  0.143148   
6          6.0  0.156861  0.135113  0.145198  0.145112  0.145107  0.145289   
7          7.0  0.154174  0.137546  0.146774  0.146788  0.146707  0.146841   
8          8.0  0.136241  0.121945  0.127560  0.127555  0.127498  0.127622   
9          9.0  0.143957  0.128904  0.134725  0.134829  0.134647  0.134804   
10        10.0  0.148993  0.126717  0.137145  0.137127  0.137066  0.137223   
11        11.0  0.137833  0.119392  0.128722  0.128749  0.128669  0.128775   
12        12.0  0.150136  0.136372  0.143336  0.143323  0.143270  0.143402   
13        13.0  0.156667  0.142747  0.149814  0.149841  0.149752  0.149876   
14        14.0  0.142559  0.129401  0.133688  0.133670  0.133621  0.133755   
15        15.0  0.146287  0.130759  0.139895  0.139942  0.139837  0.139953   
16        16.0  0.150465  0.138109  0.142194  0.142169  0.142130  0.142258   
17        17.0  0.140728  0.128681  0.134638  0.134658  0.134580  0.134696   
18        18.0  0.137989  0.127432  0.132520  0.132508  0.132462  0.132578   
19        19.0  0.144292  0.132874  0.139078  0.139100  0.139013  0.139144   
20        20.0  0.159058  0.138886  0.152374  0.152339  0.152289  0.152459   
21        21.0  0.166642  0.143586  0.157520  0.157586  0.157430  0.157610   
22        22.0  0.169035  0.150131  0.162161  0.162172  0.162075  0.162248   
23        23.0  0.162199  0.145802  0.152048  0.152082  0.151962  0.152133   
24        24.0  0.163688  0.144233  0.156921  0.156890  0.156826  0.157015   
25        25.0  0.139223  0.128984  0.133236  0.133252  0.133173  0.133299   
26        26.0  0.167684  0.147243  0.156277  0.156318  0.156203  0.156352   
27        27.0  0.163472  0.146362  0.155818  0.155804  0.155730  0.155905   

          Volume     First  350_movingaverage  111_movingaverage  \
0   2.155073e+07  0.162338           0.227809           0.186009   
1   2.117920e+07  0.133925           0.199749           0.156990   
2   2.188213e+07  0.140102           0.206574           0.168366   
3   2.452539e+07  0.136959           0.210777           0.167682   
4   1.701858e+07  0.149049           0.216571           0.171548   
5   1.496781e+07  0.146186           0.207544           0.169316   
6   2.874561e+07  0.151227           0.221842           0.180437   
7   1.807228e+07  0.146435           0.214538           0.172473   
8   1.872995e+07  0.131200           0.187993           0.146694   
9   1.969677e+07  0.139425           0.201343           0.163933   
10  4.305261e+07  0.141154           0.209549           0.170158   
11  4.131931e+07  0.125056           0.210710           0.166109   
12  2.087103e+07  0.141448           0.215223           0.176327   
13  1.685483e+07  0.149507           0.221306           0.182211   
14  2.098851e+07  0.137713           0.198349           0.156933   
15  1.673288e+07  0.138087           0.202286           0.163497   
16  1.519358e+07  0.144905           0.212432           0.174991   
17  1.673715e+07  0.135484           0.208436           0.166626   
18  1.530998e+07  0.131429           0.201399           0.159593   
19  1.783316e+07  0.139202           0.215631           0.172743   
20  3.361177e+07  0.145159           0.221364           0.178255   
21  2.248271e+07  0.152564           0.218212           0.174743   
22  2.018842e+07  0.156758           0.216614           0.177930   
23  1.577840e+07  0.157349           0.210551           0.171286   
24  1.791846e+07  0.152523           0.21

In [11]:
# # plot the moon_phase vs the daily_price_change as seperate lines with the time on the x-axis
# fig_moon_phase = make_subplots(specs=[[{"secondary_y": True}]])
# fig_moon_phase.add_trace(
#     go.Scatter(
#         x=dogeusd_data_and_moon_phase_grouped["moon_phase"],
#         y=dogeusd_data_and_moon_phase_grouped["daily_price_change"],
#         name="daily_price_change",
#         mode='lines',
#         marker=dict(color="red"),
#     )
# )

# fig_moon_phase

In [12]:
dogeusd_data_and_moon_phase["validate_ta_logic_category"] = ""
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] > 11) | (dogeusd_data_and_moon_phase["moon_phase"] <= 3), "validate_ta_logic_category"] = "long"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >3) & (dogeusd_data_and_moon_phase["moon_phase"] <=11), "validate_ta_logic_category"] = "short"
dogeusd_data_and_moon_phase

High       Low       Mid      Last       Bid       Ask  \
Date                                                                     
2021-04-22  0.310190  0.254200  0.263865  0.266120  0.263390  0.264340   
2021-04-23  0.268080  0.179490  0.243185  0.243570  0.242950  0.243420   
2021-04-26  0.280660  0.248000  0.269230  0.269110  0.268930  0.269530   
2021-04-27  0.280080  0.265080  0.271455  0.271210  0.271230  0.271680   
2021-04-28  0.344710  0.255940  0.318290  0.318830  0.318070  0.318510   
...              ...       ...       ...       ...       ...       ...   
2023-07-28  0.077977  0.076128  0.077591  0.077560  0.077570  0.077612   
2023-07-31  0.079879  0.076834  0.077784  0.077798  0.077769  0.077798   
2023-08-01  0.078382  0.075459  0.077238  0.077276  0.077199  0.077276   
2023-08-02  0.078364  0.073856  0.074621  0.074654  0.074604  0.074638   
2023-08-03  0.075092  0.072662  0.073835  0.073821  0.073813  0.073857   

                  Volume     First  350_movingaverage  111_movingaverage  \
Date                                                                       
2021-04-22  3.914806e+07  0.308760           0.266120           0.266120   
2021-04-23  7.169683e+07  0.266120           0.254845           0.254845   
2021-04-26  1.969569e+07  0.250880           0.259600           0.259600   
2021-04-27  1.280031e+07  0.269110           0.262503           0.262503   
2021-04-28  4.295062e+07  0.271210           0.273768           0.273768   
...                  ...       ...                ...                ...   
2023-07-28  4.153710e+06  0.077365           0.081208           0.074039   
2023-07-31  4.114400e+06  0.077814           0.081011           0.074009   
2023-08-01  4.528323e+06  0.077798           0.080822           0.073972   
2023-08-02  3.529204e+06  0.077276           0.080625           0.073918   
2023-08-03  3.420566e+06  0.074654           0.080439           0.073845   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2021-04-22         9.0            0.000000                0.000000   
2021-04-23        10.0           -0.084736               -0.022550   
2021-04-26        13.0            0.104857                0.025540   
2021-04-27        14.0            0.007804                0.002100   
2021-04-28        15.0            0.175583                0.047620   
...                ...                 ...                     ...   
2023-07-28         9.0            0.002521                0.000195   
2023-07-31        12.0            0.003069                0.000238   
2023-08-01        13.0           -0.006710               -0.000522   
2023-08-02        14.0           -0.033930               -0.002622   
2023-08-03        15.0           -0.011158               -0.000833   

           validate_ta_logic_category  
Date                                   
2021-04-22                      short  
2021-04-23                      short  
2021-04-26                       long  
2021-04-27                       long  
2021-04-28                       long  
...                               ...  
2023-07-28                      short  
2023-07-31                       long  
2023-08-01                       long  
2023-08-02                       long  
2023-08-03                       long  

[596 rows x 14 columns]

In [13]:
# 0 .. 6.99	New moon
# 7 .. 13.99	First quarter
# 14 .. 20.99	Full moon
# 21 .. 27.99	Last quarter
# create a new column called moon_phase_category and fill it with the moon_phase_category
dogeusd_data_and_moon_phase["moon_phase_category"] = ""
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 0) & (dogeusd_data_and_moon_phase["moon_phase"] <= 6.99), "moon_phase_category"] = "New moon"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 7) & (dogeusd_data_and_moon_phase["moon_phase"] <= 13.99), "moon_phase_category"] = "First quarter"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 14) & (dogeusd_data_and_moon_phase["moon_phase"] <= 20.99), "moon_phase_category"] = "Full moon"
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 21) & (dogeusd_data_and_moon_phase["moon_phase"] <= 27.99), "moon_phase_category"] = "Last quarter"
dogeusd_data_and_moon_phase

High       Low       Mid      Last       Bid       Ask  \
Date                                                                     
2021-04-22  0.310190  0.254200  0.263865  0.266120  0.263390  0.264340   
2021-04-23  0.268080  0.179490  0.243185  0.243570  0.242950  0.243420   
2021-04-26  0.280660  0.248000  0.269230  0.269110  0.268930  0.269530   
2021-04-27  0.280080  0.265080  0.271455  0.271210  0.271230  0.271680   
2021-04-28  0.344710  0.255940  0.318290  0.318830  0.318070  0.318510   
...              ...       ...       ...       ...       ...       ...   
2023-07-28  0.077977  0.076128  0.077591  0.077560  0.077570  0.077612   
2023-07-31  0.079879  0.076834  0.077784  0.077798  0.077769  0.077798   
2023-08-01  0.078382  0.075459  0.077238  0.077276  0.077199  0.077276   
2023-08-02  0.078364  0.073856  0.074621  0.074654  0.074604  0.074638   
2023-08-03  0.075092  0.072662  0.073835  0.073821  0.073813  0.073857   

                  Volume     First  350_movingaverage  111_movingaverage  \
Date                                                                       
2021-04-22  3.914806e+07  0.308760           0.266120           0.266120   
2021-04-23  7.169683e+07  0.266120           0.254845           0.254845   
2021-04-26  1.969569e+07  0.250880           0.259600           0.259600   
2021-04-27  1.280031e+07  0.269110           0.262503           0.262503   
2021-04-28  4.295062e+07  0.271210           0.273768           0.273768   
...                  ...       ...                ...                ...   
2023-07-28  4.153710e+06  0.077365           0.081208           0.074039   
2023-07-31  4.114400e+06  0.077814           0.081011           0.074009   
2023-08-01  4.528323e+06  0.077798           0.080822           0.073972   
2023-08-02  3.529204e+06  0.077276           0.080625           0.073918   
2023-08-03  3.420566e+06  0.074654           0.080439           0.073845   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2021-04-22         9.0            0.000000                0.000000   
2021-04-23        10.0           -0.084736               -0.022550   
2021-04-26        13.0            0.104857                0.025540   
2021-04-27        14.0            0.007804                0.002100   
2021-04-28        15.0            0.175583                0.047620   
...                ...                 ...                     ...   
2023-07-28         9.0            0.002521                0.000195   
2023-07-31        12.0            0.003069                0.000238   
2023-08-01        13.0           -0.006710               -0.000522   
2023-08-02        14.0           -0.033930               -0.002622   
2023-08-03        15.0           -0.011158               -0.000833   

           validate_ta_logic_category moon_phase_category  
Date                                                       
2021-04-22                      short       First quarter  
2021-04-23                      short       First quarter  
2021-04-26                       long       First quarter  
2021-04-27                       long           Full moon  
2021-04-28                       long           Full moon  
...                               ...                 ...  
2023-07-28                      short       First quarter  
2023-07-31                       long       First quarter  
2023-08-01                       long       First quarter  
2023-08-02                       long           Full moon  
2023-08-03                       long           Full moon  

[596 rows x 15 columns]

In [14]:
# group the dogeusd_data_and_moon_phase by the moon_phase_category column and calculate the mean of the daily_price_change and daily_price_change_abs column
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase.groupby("moon_phase_category").mean()
dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase_grouped.reset_index()
dogeusd_data_and_moon_phase_grouped

moon_phase_category      High       Low       Mid      Last       Bid  \
0       First quarter  0.147037  0.130729  0.138526  0.138544  0.138459   
1           Full moon  0.145896  0.132299  0.139175  0.139175  0.139109   
2        Last quarter  0.161608  0.143686  0.153359  0.153378  0.153277   
3            New moon  0.152311  0.136966  0.144444  0.144431  0.144370   

        Ask        Volume     First  350_movingaverage  111_movingaverage  \
0  0.138592  2.527308e+07  0.139347           0.208820           0.168386   
1  0.139240  1.949528e+07  0.138876           0.208583           0.167531   
2  0.153442  1.832457e+07  0.152551           0.216252           0.175070   
3  0.144518  2.147396e+07  0.145966           0.213325           0.171781   

   moon_phase  daily_price_change  daily_price_change_abs  
0    9.967105           -0.003042               -0.000573  
1   16.986577            0.001168                0.000759  
2   23.904762            0.001503                0.000043  
3    2.945946            0.001103               -0.001518

In [15]:
# # group the dogeusd_data_and_moon_phase by the moon_phase_category column and calculate the mean of the daily_price_change and daily_price_change_abs column
# dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase.groupby("validate_ta_logic_category").mean()
# dogeusd_data_and_moon_phase_grouped = dogeusd_data_and_moon_phase_grouped.reset_index()
# dogeusd_data_and_moon_phase_grouped
# validate_ta_logic_category	High	Low	Mid	Last	Bid	Ask	Volume	First	350_movingaverage	111_movingaverage	moon_phase	daily_price_change	daily_price_change_abs
# 0	long	0.154273	0.138621	0.146826	0.146832	0.146752	0.146901	1.979144e+07	0.146288	0.214739	0.173295	15.864286	0.001697	0.000425
# 1	short	0.149864	0.132988	0.140668	0.140678	0.140597	0.140739	2.557094e+07	0.143205	0.212704	0.170402	7.509091	-0.004078	-0.002268

In [16]:
# Correlation Analysis: First, it would be good to calculate the correlation coefficient between the moon_phase_category and the daily_price_change
# we use the pandas function corr() to calculate the correlation coefficient
dogeusd_data_and_moon_phase["daily_price_change"].corr(dogeusd_data_and_moon_phase["moon_phase"])

0.02466368299673508

In [17]:
# Regression Analysis: A linear regression model could be used to predict the BTC price change based on the moon phase. If the model is statistically significant (which you can check using a hypothesis test for the model parameters), this would suggest that there is a relationship. Moreover, the regression coefficients can be interpreted as the expected change in the BTC price for each phase of the moon.
# we use the statsmodels package to run the regression
import statsmodels.api as sm
# we need to add a constant term to the data set to estimate the intercept of the linear regression model
X = sm.add_constant(dogeusd_data_and_moon_phase["moon_phase"])
# we run the regression
model = sm.OLS(dogeusd_data_and_moon_phase["daily_price_change"], X)
results = model.fit()
# we print the summary of the regression
print(results.summary())


                            OLS Regression Results                            
Dep. Variable:     daily_price_change   R-squared:                       0.001
Model:                            OLS   Adj. R-squared:                 -0.001
Method:                 Least Squares   F-statistic:                    0.3615
Date:                Fri, 04 Aug 2023   Prob (F-statistic):              0.548
Time:                        23:21:12   Log-Likelihood:                 759.05
No. Observations:                 596   AIC:                            -1514.
Df Residuals:                     594   BIC:                            -1505.
Df Model:                           1                                         
Covariance Type:            nonrobust                                         
                 coef    std err          t      P>|t|      [0.025      0.975]
------------------------------------------------------------------------------
const         -0.0026      0.005     -0.486      0.6

In [18]:
#                          OLS Regression Results                              
# ==================================================================================
# Dep. Variable:     daily_price_change_abs   R-squared:                       0.007
# Model:                                OLS   Adj. R-squared:                  0.006
# Method:                     Least Squares   F-statistic:                     5.527
# Date:                    Thu, 20 Jul 2023   Prob (F-statistic):             0.0190
# Time:                            16:08:07   Log-Likelihood:                -6671.4
# No. Observations:                     765   AIC:                         1.335e+04
# Df Residuals:                         763   BIC:                         1.336e+04
# Df Model:                               1                                         
# Covariance Type:                nonrobust                                         
# ==============================================================================
#                  coef    std err          t      P>|t|      [0.025      0.975]
# ------------------------------------------------------------------------------
# const       -186.6173    104.328     -1.789      0.074    -391.421      18.186
# moon_phase    15.6265      6.647      2.351      0.019       2.578      28.675
# ==============================================================================
# Omnibus:                       77.255   Durbin-Watson:                   1.994
# Prob(Omnibus):                  0.000   Jarque-Bera (JB):              478.758
# Skew:                          -0.151   Prob(JB):                    1.09e-104
# Kurtosis:                       6.864   Cond. No.                         30.6
# ==============================================================================

# Notes:
# [1] Standard Errors assume that the covariance matrix of the errors is correctly specified.

# Your regression output indicates that the moon phase variable is significant at the 5% level (since the p-value, denoted as "P>|t|" for "moon_phase",
# is less than 0.05). This means there is evidence to suggest that the moon phase has some influence on the absolute daily price change of Bitcoin.

# However, be careful in interpreting the magnitude and meaning of this relationship. The coefficient for "moon_phase" is 15.6265, 
# which means that for each unit increase in moon phase, the model predicts an average increase of 15.6265 units in the absolute daily price change of Bitcoin. 
# But because moon phase is probably a categorical variable coded as numbers, it might not make much sense to think about "unit increases" in this way.

# Moreover, the R-squared value of the model is quite low (0.007), meaning that the moon phase only explains a very small portion of the variation 
# in the absolute daily price change of Bitcoin. This suggests that there are many other factors influencing Bitcoin's daily price change, 
# and that the moon phase alone is not a strong predictor.

# Also, it's important to note that this is a simple linear regression analysis, and it doesn't account for potential confounding variables or 
# other complexities of financial time-series data, such as autocorrelation or non-stationarity.

# It's also worth mentioning again that correlation does not imply causation. Just because there is a statistically significant 
# relationship between moon phase and Bitcoin's price change, it doesn't mean the moon phase is causing these price changes.
# It could be due to chance or other variables that happen to correlate with the moon phase.

In [19]:
dogeusd_data_and_moon_phase.head()

High      Low       Mid     Last      Bid      Ask  \
Date                                                                
2021-04-22  0.31019  0.25420  0.263865  0.26612  0.26339  0.26434   
2021-04-23  0.26808  0.17949  0.243185  0.24357  0.24295  0.24342   
2021-04-26  0.28066  0.24800  0.269230  0.26911  0.26893  0.26953   
2021-04-27  0.28008  0.26508  0.271455  0.27121  0.27123  0.27168   
2021-04-28  0.34471  0.25594  0.318290  0.31883  0.31807  0.31851   

                  Volume    First  350_movingaverage  111_movingaverage  \
Date                                                                      
2021-04-22  3.914806e+07  0.30876           0.266120           0.266120   
2021-04-23  7.169683e+07  0.26612           0.254845           0.254845   
2021-04-26  1.969569e+07  0.25088           0.259600           0.259600   
2021-04-27  1.280031e+07  0.26911           0.262503           0.262503   
2021-04-28  4.295062e+07  0.27121           0.273768           0.273768   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2021-04-22         9.0            0.000000                 0.00000   
2021-04-23        10.0           -0.084736                -0.02255   
2021-04-26        13.0            0.104857                 0.02554   
2021-04-27        14.0            0.007804                 0.00210   
2021-04-28        15.0            0.175583                 0.04762   

           validate_ta_logic_category moon_phase_category  
Date                                                       
2021-04-22                      short       First quarter  
2021-04-23                      short       First quarter  
2021-04-26                       long       First quarter  
2021-04-27                       long           Full moon  
2021-04-28                       long           Full moon

In [20]:
import numpy as np
import plotly.graph_objects as go
from plotly.subplots import make_subplots

# Normalizing the 'Volume'
dogeusd_data_and_moon_phase['norm_volume'] = (dogeusd_data_and_moon_phase['Volume'] - dogeusd_data_and_moon_phase['Volume'].min()) / (dogeusd_data_and_moon_phase['Volume'].max() - dogeusd_data_and_moon_phase['Volume'].min())

# Calculate daily price change
dogeusd_data_and_moon_phase['daily_change'] = dogeusd_data_and_moon_phase['Last'].diff()

# Assign colors based on positive or negative change
dogeusd_data_and_moon_phase['color'] = np.where(dogeusd_data_and_moon_phase['daily_change'] > 0, 'green', 'red')

# Create figure with secondary y-axis
fig = make_subplots(specs=[[{"secondary_y": True}]])

# Add traces
fig.add_trace(
    go.Scatter(
        x=dogeusd_data_and_moon_phase.index,
        y=dogeusd_data_and_moon_phase['Last'],
        mode='markers+lines',
        marker=dict(
            size=dogeusd_data_and_moon_phase['norm_volume']*10,  # Scale marker size
            color=dogeusd_data_and_moon_phase['color']  # Assign color based on 'daily_change'
        ),
        name='Last',
        line=dict(color='black')
    ),
    secondary_y=False
)

fig.add_trace(
    go.Bar(
        x=dogeusd_data_and_moon_phase.index,
        y=dogeusd_data_and_moon_phase['Volume'],
        name='Volume',
        marker=dict(color='black')
    ),
    secondary_y=True
)

# Add figure title and labels
fig.update_layout(
    title_text="DOGEUSD Last and Volume",
    xaxis_title="Date",
    yaxis_title="Last",
    yaxis2_title="Volume",
    xaxis_rangeslider_visible=True,
)

# Show the plot
fig.show()


In [21]:
import datetime
import requests

In [22]:
def get_binance_btcusd():
    URL = "https://api.binance.com/api/v3/klines"
    start_str = '2014-01-01 00:00:00'
    fmt = '%Y-%m-%d %H:%M:%S'
    start_time = int(time.mktime(time.strptime(start_str, fmt)) * 1000)
    last_open_time = 0  # added this line

    df = pd.DataFrame()

    while True:
        parameters = {
            'symbol': 'BTCUSDT',
            'interval': '1d',
            'startTime': start_time,
            'limit': 1000  # maximum limit
        }

        response = requests.get(URL, params=parameters)
        data = json.loads(response.text)
        
        if len(data) == 0 or last_open_time == start_time:  # updated this line
            break

        temp_df = pd.DataFrame(data, columns=['Open_time', 'Open', 'High', 'Low', 'Close', 'Volume', 
                                              'Close_time', 'Quote_asset_volume', 'Number_of_trades', 
                                              'Taker_buy_base', 'Taker_buy_quote', 'Ignore'])
        temp_df['Open_time'] = pd.to_datetime(temp_df['Open_time'], unit='ms')
        temp_df['Date'] = temp_df['Open_time'].dt.date
        temp_df['High'] = temp_df['High'].astype(float)
        temp_df['Low'] = temp_df['Low'].astype(float)
        temp_df['Last'] = temp_df['Close'].astype(float)
        temp_df['Volume'] = temp_df['Volume'].astype(float)
        temp_df['Mid'] = (temp_df['High'] + temp_df['Low']) / 2
        temp_df['First'] = temp_df['Last'].shift()

        df = pd.concat([df, temp_df])
        last_open_time = start_time  # added this line
        start_time = int(temp_df['Open_time'].dt.to_pydatetime()[-1].timestamp() * 1000) + 1

    df = df[['Date', 'High', 'Low', 'Mid', 'Last', 'Volume', 'First']]
    df.to_csv('coindata/binance_btcusdt.csv', index=False)

datasource_btcusd = "binance_btcusdt.csv"
btcusd_data = pd.read_csv("coindata/{}".format(datasource_btcusd), index_col=0)
btcusd_data.index = pd.to_datetime(btcusd_data.index)

most_recent_stored_btcusd_date = (
    btcusd_data.sort_index().tail(1).index[0].strftime("%Y-%m-%d")
)

todays_date = datetime.date.today()
todays_date = todays_date.strftime("%Y-%m-%d")


# if most_recent_stored_btcusd_date != todays_date:
# get_binance_btcusd()

# create moon diagrams

In [23]:
# 0 .. 6.99	New moon
# 7 .. 13.99	First quarter
# 14 .. 20.99	Full moon
# 21 .. 27.99	Last quarter
# create a new column called moon_phase_category and fill it with the moon_phase_category
dogeusd_data_and_moon_phase["moon_phase_category"] = ""
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 0) & (dogeusd_data_and_moon_phase["moon_phase"] <= 6.99), "moon_phase_category"] = 0
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 7) & (dogeusd_data_and_moon_phase["moon_phase"] <= 13.99), "moon_phase_category"] = 7
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 14) & (dogeusd_data_and_moon_phase["moon_phase"] <= 20.99), "moon_phase_category"] = 14
dogeusd_data_and_moon_phase.loc[(dogeusd_data_and_moon_phase["moon_phase"] >= 21) & (dogeusd_data_and_moon_phase["moon_phase"] <= 27.99), "moon_phase_category"] = 21


In [24]:
# make a new plot and plot the daily_price_change of btc by time on the x-axis
fig_btc_price_change = make_subplots(specs=[[{"secondary_y": True}]])
fig_btc_price_change.add_trace(
    go.Scatter(
        x=dogeusd_data_and_moon_phase.index,
        y=dogeusd_data_and_moon_phase["Last"],
        name="Last",
        mode='lines',
        marker=dict(color="red"),
    )
)

# now add the moon_phase column as a second y-axis
fig_btc_price_change.add_trace(
    go.Scatter(
        x=dogeusd_data_and_moon_phase.index,
        y=dogeusd_data_and_moon_phase["moon_phase_category"],
        name="moon_phase",
        mode='lines',
        marker=dict(color="blue"),
    ),
    secondary_y=True,
)

last_moon_phase = None

for i in range(len(dogeusd_data_and_moon_phase)):
    current_moon_phase = dogeusd_data_and_moon_phase['moon_phase_category'].iloc[i]
    if current_moon_phase != last_moon_phase:  # check if the moon phase category changed
        if current_moon_phase == 0:  
            fig_btc_price_change.add_annotation(
                x=dogeusd_data_and_moon_phase.index[i],
                y=0.9,
                text="🌑",
                showarrow=False,
                font=dict(
                    size=16,
                ),
                xref="x",
                yref="paper",  # Position annotation relative to the entire plot
                yanchor="bottom",  # Anchor the bottom of the text at y
            )
        elif current_moon_phase == 14: 
            fig_btc_price_change.add_annotation(
                x=dogeusd_data_and_moon_phase.index[i],
                y=0,
                text="🌕",
                showarrow=False,
                font=dict(
                    size=16,
                ),
                xref="x",
                yref="paper",  # Position annotation relative to the entire plot
                yanchor="bottom",  # Anchor the bottom of the text at y
            )
        last_moon_phase = current_moon_phase  # update the last moon phase

fig_btc_price_change

In [25]:
dogeusd_data_and_moon_phase.tail(6)

High       Low       Mid      Last       Bid       Ask  \
Date                                                                     
2023-07-27  0.080050  0.076774  0.077392  0.077365  0.077369  0.077414   
2023-07-28  0.077977  0.076128  0.077591  0.077560  0.077570  0.077612   
2023-07-31  0.079879  0.076834  0.077784  0.077798  0.077769  0.077798   
2023-08-01  0.078382  0.075459  0.077238  0.077276  0.077199  0.077276   
2023-08-02  0.078364  0.073856  0.074621  0.074654  0.074604  0.074638   
2023-08-03  0.075092  0.072662  0.073835  0.073821  0.073813  0.073857   

                  Volume     First  350_movingaverage  111_movingaverage  \
Date                                                                       
2023-07-27  4.555882e+06  0.078047           0.081360           0.074101   
2023-07-28  4.153710e+06  0.077365           0.081208           0.074039   
2023-07-31  4.114400e+06  0.077814           0.081011           0.074009   
2023-08-01  4.528323e+06  0.077798           0.080822           0.073972   
2023-08-02  3.529204e+06  0.077276           0.080625           0.073918   
2023-08-03  3.420566e+06  0.074654           0.080439           0.073845   

            moon_phase  daily_price_change  daily_price_change_abs  \
Date                                                                 
2023-07-27         8.0           -0.008738               -0.000682   
2023-07-28         9.0            0.002521                0.000195   
2023-07-31        12.0            0.003069                0.000238   
2023-08-01        13.0           -0.006710               -0.000522   
2023-08-02        14.0           -0.033930               -0.002622   
2023-08-03        15.0           -0.011158               -0.000833   

           validate_ta_logic_category moon_phase_category  norm_volume  \
Date                                                                     
2023-07-27                      short                   7     0.009556   
2023-07-28                      short                   7     0.008555   
2023-07-31                       long                   7     0.008457   
2023-08-01                       long                   7     0.009487   
2023-08-02                       long                  14     0.007001   
2023-08-03                       long                  14     0.006731   

            daily_change  color  
Date                             
2023-07-27     -0.000682    red  
2023-07-28      0.000195  green  
2023-07-31      0.000238  green  
2023-08-01     -0.000522    red  
2023-08-02     -0.002622    red  
2023-08-03     -0.000833    red

In [26]:
# Resistance Support levels automated finding

In [27]:
btcusd_data

High       Low        Mid      Last        Volume     First
Date                                                                       
2017-08-17   4485.39   4200.74   4343.065   4285.08    795.150377       NaN
2017-08-18   4371.52   3938.77   4155.145   4108.37   1199.888264   4285.08
2017-08-19   4184.69   3850.00   4017.345   4139.98    381.309763   4108.37
2017-08-20   4211.08   4032.62   4121.850   4086.29    467.083022   4139.98
2017-08-21   4119.62   3911.79   4015.705   4016.00    691.743060   4086.29
...              ...       ...        ...       ...           ...       ...
2023-07-20  30417.46  29570.96  29994.210  29800.00  37540.681930  29909.21
2023-07-21  30061.70  29726.34  29894.020  29901.72  23881.408650  29800.00
2023-07-22  29999.00  29625.10  29812.050  29794.00  14660.404670  29901.72
2023-07-23  30350.00  29730.00  30040.000  30116.01  15881.638540  29794.00
2023-07-23  30350.00  29730.00  30040.000  30116.01  15881.638540       NaN

[2170 rows x 6 columns]

In [28]:
import pandas as pd

window_length = 14  # Define a window length

# Identify resistance levels
btcusd_data['Resistance'] = btcusd_data['High'].rolling(window=window_length).max()
btcusd_data['Resistance']

Date
2017-08-17        NaN
2017-08-18        NaN
2017-08-19        NaN
2017-08-20        NaN
2017-08-21        NaN
               ...   
2023-07-20    31804.2
2023-07-21    31804.2
2023-07-22    31804.2
2023-07-23    31804.2
2023-07-23    31804.2
Name: Resistance, Length: 2170, dtype: float64

In [29]:
import pandas as pd
import numpy as np
import yfinance as yf
import plotly.graph_objects as go

num_zones = 8

data = btcusd_data

# Calculate zone range
vol_by_price = pd.cut(data['Last'], bins=num_zones).value_counts().sort_index()

# Define zones based on volume
zones = vol_by_price.index.values

# Define support and resistance levels
support_levels = [zone.left for zone in zones]
resistance_levels = [zone.right for zone in zones]

# Plot price and volume-by-price (support and resistance levels)
fig = go.Figure(data=[go.Candlestick(x=data.index,
                open=data['First'],
                high=data['High'],
                low=data['Low'],
                close=data['Last'])])

# Add support and resistance lines
for level in support_levels:
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", name=f'Support {level}'))

for level in resistance_levels:
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", name=f'Resistance {level}'))

fig.update_layout(title="only price-occurances", xaxis_rangeslider_visible=False)
fig.show()


In [30]:
support_levels

[3124.683,
 11231.121,
 19273.222,
 27315.324,
 35357.425,
 43399.526,
 51441.628,
 59483.729]

In [46]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# assuming btcusd_data is your DataFrame and it's indexed by date
data = btcusd_data

# Defining number of bars for volume profile
num_bars = 10

# Calculate frequencies of prices
vol_profile = data['Mid'].value_counts().nlargest(num_bars)

# Define support and resistance levels
support_levels = vol_profile.index.sort_values()
resistance_levels = support_levels[1:]

# Normalize volumes to range 1-5 for line widths
vol_normalized = (vol_profile - vol_profile.min()) / (vol_profile.max() - vol_profile.min()) * 4 + 1

# Plot price and volume profile (support and resistance levels)
fig = go.Figure(data=[go.Candlestick(x=data.index,
                open=data['Mid'],
                high=data['High'],
                low=data['Low'],
                close=data['Last'])])

# # Add support and resistance lines
# for level in support_levels:
#     width = vol_normalized[level]
#     fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
#                              line=dict(width=width), name=f'Support {level} Vol: {vol_profile[level]}'))

for level in resistance_levels:
    width = vol_normalized[level]
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
                             line=dict(width=width), name=f'Resistance {level} Vol: {vol_profile[level]}'))

fig.update_layout(title='BTC-USD', xaxis_rangeslider_visible=False)
fig.show()


In [56]:
import pandas as pd
import numpy as np
import plotly.graph_objects as go

# assuming btcusd_data is your DataFrame and it's indexed by date
data = btcusd_data

# Defining number of bars for volume profile
num_bars = 10

# Calculate frequencies of prices
vol_profile = data['Last'].value_counts().nlargest(num_bars)
print(vol_profile)

# Define support and resistance levels
support_levels = vol_profile.index.sort_values()
resistance_levels = support_levels[1:]

# Normalize volumes to range 1-5 for line widths
vol_normalized = (vol_profile - vol_profile.min()) / (vol_profile.max() - vol_profile.min()) * 4 + 1

# Plot price and volume profile (support and resistance levels)
fig = go.Figure(data=[go.Candlestick(x=data.index,
                open=data['First'],
                high=data['High'],
                low=data['Low'],
                close=data['Last'])])

# Add support and resistance lines
for level in resistance_levels:
    print(level)
    width = vol_normalized[level]
    print(width)
    fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
                             line=dict(width=width), name=f'Support {level} Vol: {vol_profile[level]}'))

# for level in resistance_levels:
#     width = vol_normalized[level]
#     fig.add_trace(go.Scatter(x=data.index, y=[level]*len(data.index), mode="lines", 
#                              line=dict(width=width), name=f'Resistance {level} Vol: {vol_profile[level]}'))

fig.update_layout(title='BTC-USD', xaxis_rangeslider_visible=False)
fig.show()


30116.01    2
22932.91    2
8810.79     2
6700.00     2
44850.91    1
46395.14    1
46253.40    1
43794.37    1
44572.54    1
42836.87    1
Name: Last, dtype: int64
8810.79
5.0
22932.91
5.0
30116.01
5.0
42836.87
1.0
43794.37
1.0
44572.54
1.0
44850.91
1.0
46253.4
1.0
46395.14
1.0


In [52]:
resistance_levels

Float64Index([  8753.52,   10290.0, 23088.165,   30040.0,  39341.35, 41623.145,
              43573.205,   44285.5, 44616.575],
             dtype='float64')

In [54]:
vol_normalized

30040.000    5.0
7590.000     5.0
10290.000    5.0
8753.520     5.0
23088.165    5.0
44285.500    1.0
43573.205    1.0
41623.145    1.0
39341.350    1.0
44616.575    1.0
Name: Mid, dtype: float64

In [33]:
todo zeit mit rein so wie resistence seit 2 jahren ...

SyntaxError: invalid syntax (774269896.py, line 1)